
## Using Snowflake to import new data into SC Navigator to explore new scenario's

This notebook is an example and shows how to import data from Snowflake (or another source) into SC Navigator to explore new scenario's. This example is build on a local machine which had Python installed, alternatively you can use Snowflake Worksheets or Notebooks to run this code. We used the Microsoft examples from [this link](https://learn.microsoft.com/en-us/azure/storage/blobs/data-lake-storage-directory-file-acl-python?tabs=azure-ad) to make this notebook.

#### Does this example also work outside of Snowflake?
This jupyter notebook may also work as is on your computer if you have your python environment configured and installed the required packages.

#### Prerequisites
1. Before you run this notebook you need access to the storage of you SC Navigator account. You need to generate a SAS key and write down the URL of your storage. 
2. This notebook uses the 'azure-storage-file-datalake' and the 'azure-identity' python packages. You need to install both packages to run this notebook. 


In [ ]:
%pip install azure-storage-file-datalake azure-identity

In [ ]:
from snowflake.snowpark import Session

In [ ]:
# TODO provide the connection parameters to your snowflake account
connection_parameters = {
    "user": "<put here your user>",
    "password": "<put here your password>",
    "account": "<put here your account>",
    "warehouse": "<put here your warehouse>",
    "database": "<put here your database>",
    "schema": "<put here your schema>",
}

new_session = Session.builder.configs(connection_parameters).create() 

In [ ]:
# connect to Snowflake and write the data to a table
# make sure to replace <put here your destination table name> with the name of the table you want to write to
snowpark_df = new_session.table("<put here your source table name>").collect()
df = snowpark_df.to_pandas()
# close session
new_session.close()

In [ ]:
# list of datasets to import to SC Navigator
# TODO adjust this list depending on which data you would like to upload to SC Navigator.
# NOTE you must follow the Parquet File Definition SC Navigator to make sure your data upload is succesfull
datasets = ['_dataset_info',
 'bill_of_material',
 'custom_objective',
 'customer_definition',
 'customer_groups',
 'customer_product',
 'inventory_product_step',
 'inventory_step',
 'location_definition',
 'location_groups',
 'location_period',
 'location',
 'mode_of_transport_definition',
 'mode_of_transport_product',
 'period_definition',
 'product_definition',
 'product_groups',
 'production_bom',
 'production_definition',
 'production_groups',
 'production_routing',
 'production_step',
 'settings',
 'supplier_definition',
 'supplier_product_step',
 'supplier_step',
 'transport_trip_data',
 'uom_product',
 'warehouse_definition',
 'warehouse_groups',
 'warehouse_product_step',
 'warehouse_step']

In the next cell we load the datasets which we would like to import into SC Navigator. We do some transformations because tables cannot work with spaces and parenthesis. We used placeholder tokens and now we map these tokens to the required columns names and dataset names as specifed in the Parquet File Definition SC Navigator.

In [ ]:
# get the prepared data from Snowflake and do some transformations
import numpy as np
dataframes_for_input = dict()
new_session = Session.builder.configs(connection_parameters).create() 
for dataset in datasets:
    # load the data
    snowpark_df = new_session.table("<put here your source schema name>." + dataset).collect()
    df = snowpark_df.to_pandas()
    # transform to the Parquet File Definition SC Navigator definition
    df.columns = [x.replace("_", " ") for x in df.columns]
    df.columns = [x.replace(".", "(") for x in df.columns]
    df.columns = [x.replace("-", ")") for x in df.columns]
    df = df.replace({np.nan: None})
    if dataset != "_dataset_info":
        dataset = dataset.replace("_", "-")
    # store result
    dataframes_for_input[dataset] = df
# close session
new_session.close()

In [ ]:
# show all datasets  
[k for k,v in dataframes_for_input.items()]

Now its time to connect to Azure Data Lake Storage and upload our datasets

In [ ]:
# TODO: provide the sas token and the URL of your storage
account_url_full = "<put here your URL>"
# remove the folder from the url
account_url = account_url_full[:-20]
sas_token = "<put here your sas token>"
# the file system is fixed, this is the container SC Navigator will write its results
file_system="sc-navigator-import"

In [ ]:
# import required packages
import os
from azure.storage.filedatalake import (
    DataLakeServiceClient,
    DataLakeDirectoryClient,
    FileSystemClient
)
from azure.identity import DefaultAzureCredential

In [ ]:
# create a DataLakeServiceClient to access the storage 
dsc = DataLakeServiceClient(account_url=account_url, credential=sas_token)

In [ ]:
# list all folders/files on the storage
file_system_client = dsc.get_file_system_client(file_system=file_system)
paths = file_system_client.get_paths()
list_of_files = list()
for path in paths:
    if "/" not in path.name and path.name != "info.txt":
        print(path.name + '\n')
        list_of_files.append(path.name)
    else:
        continue

In [ ]:
# create a new directory to store the datasets
directory_name = "<directory name>"
dld_client = file_system_client.create_directory(directory_name)

In [ ]:
# NOTE if you make a mistake our would like to upluad other data you can delete a folder 
client = dsc.get_directory_client(file_system=file_system,directory="<directory name>")
client.delete_directory()

In [ ]:
#inspect _dataset_infor before actual upload. Note that the Dataset field will be used to identify the uploaded data in SC Navigator
dataframes_for_input["_dataset_info"]

In [ ]:
# upload the files for the selected scenario's
client = dld_client
for k,v in dataframes_for_input.items():
    file_name = k + ".parquet"
    file_client = client.create_file(file_name)
    bytes_data = v.to_parquet()
    file_client.append_data(data=bytes_data, offset=0, length=len(bytes_data))
    file_client.flush_data(len(bytes_data))


## Remarks

If you would like to check if the upload went well you can use the cell below to check the _dataset_info file on ADLS directly

In [ ]:
import io
import pandas as pd
file_client = client.get_file_client("_dataset_info.parquet")
data_file = file_client.download_file()
data_binary = data_file.readall()
parquet_file = io.BytesIO(data_binary)
df = pd.read_parquet(parquet_file)
display(df)

Congratulations! You just uploaded data from Snowflake to SC Navigator. Now open the System Configuration app (or ask you admin to do this) and push the rebuild overview botton on the File System Management tab. If you now open SC Navigator you should see that your dataset is added to the overview.  